### We want to change the getdata api calls from amda url, to speasy library.

#### First we take a look at how it was done, and what 

In [3]:
import os
import sys
import matplotlib.pyplot as plt
from datetime import datetime
from speasy import amda
import pandas as pd



#
# Heliopropa imports
#

# try to tweak the logging system first
#
os.environ['DEBUG'] = '1'

sys.path.insert(0, os.path.abspath('..'))
from web.run import get_target_config, get_data_for_target, FILE_DATE_FMT, generate_csv_contents

##### Configure dates targets and inputs

In [4]:
# 
_target_slug = "mars"
_input_slug = "om"
_start_time =  datetime.strptime('20230101', '%Y%m%d')
_stop_time =  datetime.strptime('20230401', '%Y%m%d')

##### Get data with old method (amda http requests)

Returns dictionnary of tupples indexed by dates.
Each tuple contains 10 values:


time,vrad,vtan,vtot,btan,temp,pdyn,dens,atse,xhee,yhee

In [5]:
target_config = get_target_config( _target_slug)
all_data = get_data_for_target(target_config, _input_slug, _start_time, _stop_time )

AttributeError: 'Exception' object has no attribute 'message'

In [ ]:
# display first elements of the all_data retrieved this way
small_data_keys = list(all_data.keys())[0:5]
for k in small_data_keys:
    # dont display first tuple element that is date
    print(k, all_data[k][1:])

In [ ]:
# same with the calling method
all_csv = generate_csv_contents(_target_slug, _input_slug, _start_time, _stop_time)


In [ ]:
print(all_csv[0:600])

#### Now rewrite that with speazy

ie, generate a csv file with that new library.p
That means getting parameters, rename the column as expected by the javascript grappher,
and concatenate to get a single dataframe.

In [ ]:
# First, get the dataset ids 
target_config = get_target_config(_target_slug)
orbit_dataset_id = target_config['orbit']['models'][0]['slug']
plasma_dataset_id = target_config['models'][_input_slug][0]['slug']
orbit_dataset_id = orbit_dataset_id.replace('_', '-')
plasma_dataset_id = plasma_dataset_id.replace('_', '-')

print(f"Orbit dataset : {orbit_dataset_id}")
print(f"Plsama dataset : {plasma_dataset_id}")


In [ ]:
# Then the dataset associated
orbit_dataset = amda.get_dataset(orbit_dataset_id, _start_time, _stop_time)
plasma_dataset = amda.get_dataset(plasma_dataset_id, _start_time, _stop_time)

In [17]:
# vrad, vtan, vtot, btan, brad, pdyn, dens, atse, xhee, yhee

# set a dict of amda parameters ids index by the expected column names in the csv

params_dict =  {'dens': 'mars_sw_n',
                'xy_v': 'mars_sw_v',
                'temp': 'mars_sw_t',
                'pdyn': 'mars_sw_pdyn',
                'btan': 'mars_sw_b',
                'brad': 'mars_sw_bx',
                'atse': 'mars_sw_da',
                'xy_hee': 'xyz_mars_hee'}

list_df = []
for _name, _id in params_dict.items():
    _df = amda.get_data(_id, _start_time, _stop_time).to_dataframe()
    if _name == 'xy_v':
        _df = _df.rename(columns={_df.columns[0]:'vrad', _df.columns[1]:'vtan'})
    elif _name == 'xy_hee':
        _df = _df.drop(_df.columns[2], axis=1)
        _df = _df.rename(columns={_df.columns[0]:'xhee', _df.columns[1]:'yhee'})
    else:
        _df = _df.rename(columns={_df.columns[0]: _name})

    # _df = _df[~_df.index.duplicated()]

    # resample to frequency, for later concatenation
    _df = _df.resample('1H').mean()

    # _df = _df.loc[_df.first_valid_index():_df.last_valid_index()]

    list_df.append( _df)



In [ ]:
from math import sqrt
final_df = pd.concat(list_df, axis=1)
# Is ther a vtot param ? else build it
if 'vtot' not in final_df.columns:
    final_df['vtot'] = final_df.apply(lambda x: sqrt(x.vtan*x.vtan+ x.vrad*x.vrad), axis=1)

cols_ordered = ['vrad', 'vtan', 'vtot', 'btan', 'brad', 'temp', 'pdyn', 'dens', 'atse', 'xhee', 'yhee']
final_df = final_df[cols_ordered]

# and show
pd.set_option('display.max_columns', None)
print(final_df.head())

In [21]:
final_df.index.name = 'time'
print(final_df.index.name)

time


#### Use config to get the parameters dict and send to new method


In [24]:
def generate_csv_content_spz(target_slug, input_slug, started_at, stopped_at):
    target_config = get_target_config(target_slug)
    params_dict = target_config['models'][input_slug][0]['parameters']
    
    list_df = []
    for _name, _id in params_dict.items():
        _df = amda.get_data(_id, _start_time, _stop_time).to_dataframe()
        if _name == 'xy_v':
            _df = _df.rename(columns={_df.columns[0]:'vrad', _df.columns[1]:'vtan'})
        elif _name == 'xy_hee':
            _df = _df.drop(_df.columns[2], axis=1)
            _df = _df.rename(columns={_df.columns[0]:'xhee', _df.columns[1]:'yhee'})
        else:
            _df = _df.rename(columns={_df.columns[0]: _name})
    
        # _df = _df[~_df.index.duplicated()]
    
        # resample to frequency, for later concatenation
        _df = _df.resample('1H').mean()
    
        # _df = _df.loc[_df.first_valid_index():_df.last_valid_index()]
    
        list_df.append( _df)
    
    from math import sqrt
    final_df = pd.concat(list_df, axis=1)
    # Is ther a vtot param ? else build it
    if 'vtot' not in final_df.columns:
        final_df['vtot'] = final_df.apply(lambda x: sqrt(x.vtan*x.vtan+ x.vrad*x.vrad), axis=1)
        
    
    cols_ordered = ['vrad', 'vtan', 'vtot', 'btan', 'brad', 'temp', 'pdyn', 'dens', 'atse', 'xhee', 'yhee']
    final_df = final_df[cols_ordered]
    final_df.index.name = 'time'
    return final_df.to_csv(date_format='%Y-%m-%dT%H:%M:%S', float_format="%.5f",
                      header=True,
                      sep=",")


In [25]:
generate_csv_content_spz('mars', 'om', '20230101', '20230115')

'time,vrad,vtan,vtot,btan,brad,temp,pdyn,dens,atse,xhee,yhee\n2023-01-01T00:00:00,458.53900,-8.99439,458.62721,-1.89241,0.49059,6.42018,0.71353,2.02797,10.37680,1.52861,-0.33055\n2023-01-01T01:00:00,539.66600,-18.05740,539.96802,-2.59106,2.10203,10.00060,0.72163,1.48205,10.66710,1.52853,-0.33114\n2023-01-01T02:00:00,543.80100,-16.74380,544.05871,-2.52267,2.06216,9.38966,0.65580,1.32666,10.68800,1.52845,-0.33173\n2023-01-01T03:00:00,547.86400,-13.52640,548.03095,-2.50299,2.06129,8.68052,0.63815,1.27231,10.70950,1.52837,-0.33233\n2023-01-01T04:00:00,549.25800,-4.20118,549.27407,-2.48744,2.05363,7.80526,0.62965,1.24969,10.73160,1.52830,-0.33292\n2023-01-01T05:00:00,548.67600,5.81362,548.70680,-2.46739,2.03485,6.73197,0.64252,1.27788,10.75300,1.52822,-0.33351\n2023-01-01T06:00:00,546.76300,8.89294,546.83532,-2.38355,1.95879,6.23209,0.62952,1.26060,10.77400,1.52814,-0.33411\n2023-01-01T07:00:00,548.76000,8.77561,548.83016,-2.44846,2.01942,6.44499,0.66720,1.32637,10.79620,1.52806,-0.33470\n2